# Maps
We often deal with data that has a geographical element.  In order to communicate this kind of data, we can use maps.  At face value, maps are a simple and easy way to consume data, however, as programmers, they can be tricky to program.  Luckily for us, there are packages like folium, pyploy that do a lot of the heavy lifting for us.

This notebook provides you with a basic demo in programming maps in python.


We begin by importing the relevant packages

In [2]:
%matplotlib inline
import chart_studio.plotly as py
import pandas as pd # library for data analysis
import numpy as np
import json # library to handle JSON files
import plotly.express as px
import requests # library to handle requests
import folium # map rendering library
import streamlit as st #creating an app


We can generate a world map with the following.

In [14]:
# define the world map
world_map = folium.Map()
# display world map
world_map

Our goal is to create a map that conveys the population of New Zealand by region in 2013.  To begin, we use the read_csv() function from the pandas library, which reads a csv file and generates a DataFrame object.  

In [4]:
dddd = pd.read_csv("Census_Population_by_age_by_Regional_Council_2001_2006_2013.csv")

dddd

Region        Region Code  Year  \
0       Northland   Northland Region  2001   
1       Northland   Northland Region  2001   
2       Northland   Northland Region  2001   
3       Northland   Northland Region  2001   
4       Northland   Northland Region  2001   
...           ...                ...   ...   
1021  New Zealand  Total New Zealand  2006   
1022  New Zealand  Total New Zealand  2013   
1023  New Zealand  Total New Zealand  2013   
1024  New Zealand  Total New Zealand  2013   
1025  New Zealand  Total New Zealand  2013   

                                                Measure           Age  \
0     Age in five-year groups for the census usually...           0-4   
1     Age in five-year groups for the census usually...           5-9   
2     Age in five-year groups for the census usually...         10-14   
3     Age in five-year groups for the census usually...         15-19   
4     Age in five-year groups for the census usually...         20-24   
...                                                 ...           ...   
1021  Age in broad groups for the census usually res...  Total people   
1022  Age in broad groups for the census usually res...          *-14   
1023  Age in broad groups for the census usually res...         15-64   
1024  Age in broad groups for the census usually res...          65-*   
1025  Age in broad groups for the census usually res...  Total people   

        Value Value Unit       Value Label  Null Reason  
0       10446     number  Number of people          NaN  
1       12210     number  Number of people          NaN  
2       12522     number  Number of people          NaN  
3        9204     number  Number of people          NaN  
4        6213     number  Number of people          NaN  
...       ...        ...               ...          ...  
1021  4027947     number  Number of people          NaN  
1022   865632     number  Number of people          NaN  
1023  2769384     number  Number of people          NaN  
1024   607032     number  Number of people          NaN  
1025  4242048     number  Number of people          NaN  

[1026 rows x 9 columns]

We will now like to manipulate the data and extract the inormation that will help with our analysis.  Since we want to measure the population in 2013, we only want the data with "total people" in the age column, and 2013 in the year coloumn.  Below is a straightforward way of how we do this. 

In [5]:
dddd = dddd[dddd.Age == "Total people"]
dddd = dddd[dddd.Year == 2013]
dddd = dddd[dddd.Measure == "Age in five-year groups for the census usually resident population count"]
dddd

Region               Region Code  Year  \
44             Northland          Northland Region  2013   
101             Auckland           Auckland Region  2013   
158              Waikato            Waikato Region  2013   
215        Bay of Plenty      Bay of Plenty Region  2013   
272             Gisborne           Gisborne Region  2013   
329          Hawke's Bay        Hawke's Bay Region  2013   
386             Taranaki           Taranaki Region  2013   
443   Manawatū-Whanganui  Manawatu-Wanganui Region  2013   
500           Wellington         Wellington Region  2013   
557               Tasman             Tasman Region  2013   
614               Nelson             Nelson Region  2013   
671          Marlborough        Marlborough Region  2013   
728           West Coast         West Coast Region  2013   
785           Canterbury         Canterbury Region  2013   
842                Otago              Otago Region  2013   
899            Southland          Southland Region  2013   
956      Chatham Islands       Area Outside Region  2013   
1013         New Zealand         Total New Zealand  2013   

                                                Measure           Age  \
44    Age in five-year groups for the census usually...  Total people   
101   Age in five-year groups for the census usually...  Total people   
158   Age in five-year groups for the census usually...  Total people   
215   Age in five-year groups for the census usually...  Total people   
272   Age in five-year groups for the census usually...  Total people   
329   Age in five-year groups for the census usually...  Total people   
386   Age in five-year groups for the census usually...  Total people   
443   Age in five-year groups for the census usually...  Total people   
500   Age in five-year groups for the census usually...  Total people   
557   Age in five-year groups for the census usually...  Total people   
614   Age in five-year groups for the census usually...  Total people   
671   Age in five-year groups for the census usually...  Total people   
728   Age in five-year groups for the census usually...  Total people   
785   Age in five-year groups for the census usually...  Total people   
842   Age in five-year groups for the census usually...  Total people   
899   Age in five-year groups for the census usually...  Total people   
956   Age in five-year groups for the census usually...  Total people   
1013  Age in five-year groups for the census usually...  Total people   

        Value Value Unit       Value Label  Null Reason  
44     151689     number  Number of people          NaN  
101   1415550     number  Number of people          NaN  
158    403638     number  Number of people          NaN  
215    267744     number  Number of people          NaN  
272     43653     number  Number of people          NaN  
329    151179     number  Number of people          NaN  
386    109608     number  Number of people          NaN  
443    222672     number  Number of people          NaN  
500    471315     number  Number of people          NaN  
557     47154     number  Number of people          NaN  
614     46437     number  Number of people          NaN  
671     43416     number  Number of people          NaN  
728     32148     number  Number of people          NaN  
785    539433     number  Number of people          NaN  
842    202470     number  Number of people          NaN  
899     93342     number  Number of people          NaN  
956       600     number  Number of people          NaN  
1013  4242048     number  Number of people          NaN

geojson is a format the encodes goegrahical features.  The 'nz_region.geojson' file contains regional border information.  Every region has its corresponding borders encoded so that we can 

In [12]:
with open('nz_region.geojson') as file:
    nz = json.load(file)

Now that we have all the information we need, we can actually generate the map.  The documentation can be found here https://plotly.github.io/plotly.py-docs/generated/plotly.express.choropleth_mapbox.html.  

In [13]:


fig = px.choropleth_mapbox(dddd, geojson=nz, 
                           locations='Region Code', #name of the feature that contains the regions in dddd
                           color='Value', #the value that we want to represent; in our case, population.  
                           color_continuous_scale="Viridis", # colour of represntation
                           range_color=(0, 1800000),
                           mapbox_style="carto-positron",
                           zoom=3, #the initial zoom
                           center = {"lat": 37.0902, "lon": -95.7129}, #the initial coordinates for the map
                           opacity=0.5,
                           labels={'Value':'Population'},
                           featureidkey = "properties.REGC2016_N" # the feature in the geojson file that corresponds to the locations.
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()